In [1]:
import nltk
nltk.download('punkt')

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


True

In [2]:
!pip install flask-ngrok
!pip install pyngrok


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 718.7/718.7 kB 7.0 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for pyngrok: filename=pyngrok-7.0.0-py3-none-any.whl size=21129 sha256=ca9e8982547a8b26d9f24f46878007845a23516787ff62220cfd84e304701884
  Stored in directory: /root/.cache/pip/wheels/60/29/7b/f64332aa7e5e88fbd56d4002185ae22dcdc83b35b3d1c2cbf5
Successfully built pyngrok


In [3]:
!ngrok authtoken '2XRS0K8EGeMnBfSxVE01Z7aL31i_tjnj9FyGMRfwqk8Ddsrr'
from flask import Flask, request, jsonify
from flask_ngrok import run_with_ngrok

Authtoken saved to configuration file: /root/.ngrok2/ngrok.yml


In [4]:

!pip install flask

In [5]:
!pip install streamlit

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.4/8.4 MB 62.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 190.6/190.6 kB 22.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.8/4.8 MB 109.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 82.1/82.1 kB 10.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.7/62.7 kB 8.3 MB/s eta 0:00:00


In [6]:
!pip install flask-ngrok

In [7]:
pip install transformers

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.7/7.7 MB 59.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 302.0/302.0 kB 37.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.8/3.8 MB 105.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 71.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 295.0/295.0 kB 35.2 MB/s eta 0:00:00


In [8]:
from transformers import AutoTokenizer

# Define the model and tokenizer names
model_name = "pszemraj/led-large-book-summary"
tokenizer = AutoTokenizer.from_pretrained(model_name)

In [9]:
from transformers import AutoModelForSeq2SeqLM, AutoTokenizer
import torch

device = "cuda" if torch.cuda.is_available() else "cpu"

In [10]:
from transformers import pipeline

summarizer = pipeline("summarization", model="pszemraj/led-large-book-summary", device=0 if torch.cuda.is_available() else -1)

In [11]:
from flask import Flask, request, jsonify
from flask_ngrok import run_with_ngrok
import streamlit as st
import requests
from bs4 import BeautifulSoup
import difflib

In [12]:
import requests
from bs4 import BeautifulSoup
import difflib

# Function to search for a book by name and return the best match URL
def search_book_by_name(book_name):
    base_url = "https://www.gutenberg.org/"
    search_url = base_url + "ebooks/search/?query=" + book_name.replace(" ", "+") + "&submit_search=Go%21"

    response = requests.get(search_url)
    soup = BeautifulSoup(response.content, "html.parser")

    # Find the best match link based on similarity ratio
    best_match_ratio = 0
    best_match_url = ""

    for link in soup.find_all("li", class_="booklink"):
        link_title = link.find("span", class_="title").get_text()
        similarity_ratio = difflib.SequenceMatcher(None, book_name.lower(), link_title.lower()).ratio()
        if similarity_ratio > best_match_ratio:
            best_match_ratio = similarity_ratio
            best_match_url = base_url + link.find("a").get("href")

    return best_match_url

# Function to get the "Plain Text UTF-8" download link from the book page
def get_plain_text_link(book_url):
    response = requests.get(book_url)
    soup = BeautifulSoup(response.content, "html.parser")

    plain_text_link = ""

    for row in soup.find_all("tr"):
        format_cell = row.find("td", class_="unpadded icon_save")
        if format_cell and "Plain Text UTF-8" in format_cell.get_text():
            plain_text_link = format_cell.find("a").get("href")
            break

    return plain_text_link


# Function to get the content of the "Plain Text UTF-8" link
def get_plain_text_content(plain_text_link):
    response = requests.get(plain_text_link)
    content = response.text
    return content
def get_sentences(book_name):
    print(book_name)
    best_match_url = search_book_by_name(book_name)
    if best_match_url:
        plain_text_link = get_plain_text_link(best_match_url)
        if plain_text_link:
            full_plain_text_link = "https://www.gutenberg.org" + plain_text_link
            FileContent = get_plain_text_content(full_plain_text_link)
            # unstring "plain_text_content" to print the whole book
            FileContent = FileContent.split("*** START OF THE PROJECT GUTENBERG EBOOK")[1]
            FileContent = FileContent.split("*** END OF THE PROJECT GUTENBERG EBOOK THE PRINCE")[0]
            # extract the sentences from the document
            sentences = nltk.tokenize.sent_tokenize(FileContent)
            return sentences
        else:
            print("No Plain Text UTF-8 link found.")
    else:
        print("No matching book found.")
def get_chunks(sentences):
    length = 0
    chunk = ""
    chunks = []
    count = -1
    for sentence in sentences:
        count += 1
        combined_length = len(tokenizer.tokenize(sentence)) + length # add the no. of sentence tokens to the length counter
        if combined_length  <= tokenizer.max_len_single_sentence: # if it doesn't exceed
            chunk += sentence + " " # add the sentence to the chunk
            length = combined_length # update the length counter

            # if it is the last sentence
            if count == len(sentences) - 1:
              chunks.append(chunk.strip()) # save the chunk

        else:
            chunks.append(chunk.strip()) # save the chunk

          # reset
            length = 0
            chunk = ""

            # take care of the overflow sentence
            chunk += sentence + " "
            length = len(tokenizer.tokenize(sentence))
    return chunks

def generate_summary(chunks):
    i=0
    for inputs in chunks:
        i+=1
        summary = summarizer(inputs, max_length=150, min_length=30,
                          no_repeat_ngram_size=3,
                          encoder_no_repeat_ngram_size=3,
                          repetition_penalty=3.5,
                          num_beams=4,
                          do_sample=False)
        final_summary = summary[0]['summary_text']
        return final_summary

# Tested book names
#     -The changed brides
#     -The bride's fate

In [13]:
pip install pyngrok

In [14]:
from flask import Flask

In [ ]:
# Import your summarization and Q/A models here
# Replace these with your actual model import code
app = Flask(__name__)
run_with_ngrok(app)
@app.route('/')
def home():
    return "Homepage of Book Summarization"
@app.route('/get_summary', methods=['POST'])
def get_summary():
    try:
        data = request.get_json()
        book_name = data['book_name']
        print(book_name)
        sentences = get_sentences(book_name)
        print(sentences)
        chunks = get_chunks(sentences)
        summary = generate_summary(chunks)
        return jsonify({"summary": summary})
    except Exception as e:
        return jsonify({'error': str(e)}), 500
# @app.route('/get_answer', methods=['POST'])
# def get_answer():
#     data = request.get_json()
#     book_name = data['book_name']
#     question = data['question']
#     answer = answer_question(book_name, question)
#     return jsonify({"answer": answer})

if __name__ == '__main__':
    app.run()


 * Serving Flask app '__main__'
 * Debug mode: off


INFO:werkzeug:WARNING: This is a development server. Do not use it in a production deployment. Use a production WSGI server instead.
 * Running on http://127.0.0.1:5000
INFO:werkzeug:Press CTRL+C to quit


 * Running on http://c860-34-68-80-109.ngrok-free.app
 * Traffic stats available on http://127.0.0.1:4040
The changed brides
The changed brides
[' THE CHANGED BRIDES ***\r\n\r\n\r\n\r\n\r\n                          THE CHANGED BRIDES.', 'BY\r\n\r\n                      MRS. EMMA D. E. N. SOUTHWORTH.', 'AUTHOR OF “HOW HE WON HER,” “FAIR PLAY,” “THE BRIDES’ FATE,” “THE\r\n    DISCARDED DAUGHTER,” “HAUNTED HOMESTEAD,” “RETRIBUTION,” “THE LOST\r\n HEIRESS,” “THE FORTUNE SEEKER,” “ALLWORTH ABBEY,” “THE FATAL MARRIAGE,”\r\n  “THE MISSING BRIDE,” “THE TWO SISTERS,” “THE BRIDAL EVE,” “LADY OF THE\r\n  ISLE,” “GIPSY’S PROPHECY,” “VIVIA,” “WIFE’S VICTORY,” “MOTHER-IN-LAW,”\r\n   “INDIA,” “THE THREE BEAUTIES,” “THE CURSE OF CLIFTON,” “THE DESERTED\r\n   WIFE,” “LOVE’S LABOR WON,” “FALLEN PRIDE,” “THE BRIDE OF LLEWELLYN,”\r\n                 “THE WIDOW’S SON,” “PRINCE OF DARKNESS.”\r\n\r\n\r\n                ’TIS AN OLD TALE, AND OFTEN TOLD—\r\n                A MAIDEN TRUE, BETRAYED FOR GOLD.—SCO

INFO:werkzeug:127.0.0.1 - - [30/Oct/2023 13:03:58] "POST /get_summary HTTP/1.1" 200 -


The changed brides
The changed brides
[' THE CHANGED BRIDES ***\r\n\r\n\r\n\r\n\r\n                          THE CHANGED BRIDES.', 'BY\r\n\r\n                      MRS. EMMA D. E. N. SOUTHWORTH.', 'AUTHOR OF “HOW HE WON HER,” “FAIR PLAY,” “THE BRIDES’ FATE,” “THE\r\n    DISCARDED DAUGHTER,” “HAUNTED HOMESTEAD,” “RETRIBUTION,” “THE LOST\r\n HEIRESS,” “THE FORTUNE SEEKER,” “ALLWORTH ABBEY,” “THE FATAL MARRIAGE,”\r\n  “THE MISSING BRIDE,” “THE TWO SISTERS,” “THE BRIDAL EVE,” “LADY OF THE\r\n  ISLE,” “GIPSY’S PROPHECY,” “VIVIA,” “WIFE’S VICTORY,” “MOTHER-IN-LAW,”\r\n   “INDIA,” “THE THREE BEAUTIES,” “THE CURSE OF CLIFTON,” “THE DESERTED\r\n   WIFE,” “LOVE’S LABOR WON,” “FALLEN PRIDE,” “THE BRIDE OF LLEWELLYN,”\r\n                 “THE WIDOW’S SON,” “PRINCE OF DARKNESS.”\r\n\r\n\r\n                ’TIS AN OLD TALE, AND OFTEN TOLD—\r\n                A MAIDEN TRUE, BETRAYED FOR GOLD.—SCOTT.', 'PHILADELPHIA:\r\n                       T. B. PETERSON & BROTHERS;\r\n                          306

...

INFO:werkzeug:127.0.0.1 - - [30/Oct/2023 13:09:40] "POST /get_summary HTTP/1.1" 200 -


Jane Eyre: An Autobiography
Jane Eyre: An Autobiography
[' JANE EYRE: AN AUTOBIOGRAPHY ***\r\n\r\n\r\n\r\nJANE EYRE\r\nAN AUTOBIOGRAPHY\r\n\r\nby Charlotte Brontë\r\n\r\n_ILLUSTRATED BY F. H. TOWNSEND_\r\n\r\nLondon\r\nSERVICE & PATON\r\n5 HENRIETTA STREET\r\n1897\r\n\r\n_The Illustrations_\r\n_in this Volume are the copyright of_\r\nSERVICE & PATON, _London_\r\n\r\nTO\r\nW. M. THACKERAY, ESQ.,\r\n\r\nThis Work\r\nIS RESPECTFULLY INSCRIBED\r\n\r\nBY\r\nTHE AUTHOR\r\n\r\n\r\n\r\n\r\nPREFACE\r\n\r\n\r\nA preface to the first edition of “Jane Eyre” being unnecessary, I gave\r\nnone: this second edition demands a few words both of acknowledgment\r\nand miscellaneous remark.', 'My thanks are due in three quarters.', 'To the Public, for the indulgent ear it has inclined to a plain tale\r\nwith few pretensions.', 'To the Press, for the fair field its honest suffrage has opened to an\r\nobscure aspirant.', 'To my Publishers, for the aid their tact, their energy, their practical\r\nsense and fr

INFO:werkzeug:127.0.0.1 - - [30/Oct/2023 13:20:52] "POST /get_summary HTTP/1.1" 200 -


The bride's fate
The bride's fate
[" THE BRIDE'S FATE ***\r\n\r\n\r\n\r\n\r\n                           _THE BRIDE’S FATE_\r\n                   The Sequel to “The Changed Brides”\r\n\r\n\r\n                                  _By_\r\n                      MRS. E. D. E. N. SOUTHWORTH\r\n\r\n                               AUTHOR OF\r\n\r\n “A Leap in the Dark,” “The Lost Lady of Lone,” “Nearest and Dearest,”\r\n  “Her Mother’s Secret,” “A Beautiful Fiend,” “Victor’s Triumph,” Etc.", '[Illustration]\r\n\r\n             _I have set my life upon a cast,\r\n             And I will abide the hazard of the die._\r\n                                             —SHAKESPEARE.', 'A. L. BURT COMPANY\r\n                        PUBLISHERS      NEW YORK\r\n\r\n\r\n\r\n\r\n                             POPULAR BOOKS\r\n\r\n                     By MRS. E. D. E. N. SOUTHWORTH\r\n\r\n                       In Handsome Cloth Binding\r\n\r\n                   Price per volume,        60 Cents\r\n\r\n\r\n     

INFO:werkzeug:127.0.0.1 - - [30/Oct/2023 13:23:47] "POST /get_summary HTTP/1.1" 200 -
